In [ ]:
"""
Please save notebooks with important results to your own folder in JupyterHub.
See README for usage instructions:
https://git.zooxlabs.com/zooxco/driving/tree/master/mined_metric/jupyter/README.md
"""
from mined_metric.jupyter.utils.data_access_util import get_experiment_data, chum_summary_stats
import pandas as pd
import matplotlib.pyplot as plt
import math
import numpy as np
import urllib
from IPython.display import IFrame
import sys
from data.chum import chumpy

EXPERIMENT_ID = "EXPERIMENT_ID_PLACEHOLDER"

In [ ]:
%%sh
pip install seaborn

In [ ]:
sys.path.insert(0,'/home/zoox/.local/lib/python2.7/site-packages')
import seaborn as sns

In [ ]:
exp_data = get_experiment_data(EXPERIMENT_ID)

In [ ]:
def filterExpData(exp_data):
    filtered = []
    data = exp_data['meta']
    for d in data:
        if 'sim_failed' in d:
            continue
            
        if d['distance_min_margin'] > 0.0 and d['first_distance_to_target'] > 0.0 and d['follow_duration'] > 1.0 and d['entity_velocity_min_margin'] > 1.0 and d['hero_velocity_min_margin'] > 1.0:
            for r in d['raw_data']:
                r['timestamp'] = float(r['timestamp'])
            filtered.append(d)
    
    print('got ' + str(len(filtered)) + ' follow events.')
    return filtered

In [ ]:
x = filterExpData(exp_data)
df = pd.DataFrame(x)

In [ ]:
# colored_scatter() and colored_line() are seaborn helper functions that are used 
# to help plot the joint distributions in the compare_distributions_plot() function.
def colored_scatter(x, y, c=None):
    def scatter(*args, **kwargs):
        plt.scatter(x, y, c=c, alpha=0.5, marker='.')
    return scatter
    
def colored_line(r):
    def plot(*args, **kwargs):
        xy = range(r)
        plt.plot(xy, xy, c='k', alpha=0.7, linestyle='--', label='_nolegend_')
    return plot

def plot_dist(data, comments, title=None, xlabel=None):
    plt.figure(figsize=(9,5))
    for d in data:
        sns.distplot(d, bins=30)
        
    sns.despine(left=True)
    plt.yticks([])
    
    if xlabel:
        plt.xlabel(xlabel)
    
    if title:
        plt.title(title)
        
    plt.legend(comments)
    plt.show()
    
def compare_distributions_plot(dfs, columns, comments=['autonomous', 'manual']):
    assert len(columns) == 2
    
    colors = ['g', 'b', 'r', 'c', 'y', 'm']
    colors_idx = 0
    g = sns.JointGrid([], [])
    p = int(max([df[columns[0]].max() for df in dfs]))+2
    g = g.plot_joint(colored_line(p))
    for df in dfs:
        g = g.plot_joint(colored_scatter(df[columns[0]], df[columns[1]], colors[colors_idx]))
        colors_idx += 1
        
    colors_idx = 0
    
    for df in dfs:
        sns.distplot(df[columns[0]], ax=g.ax_marg_x, color=colors[colors_idx])
        colors_idx += 1
        
    colors_idx = 0
    
    for df in dfs:
        sns.distplot(df[columns[1]], ax=g.ax_marg_y, vertical=True, color=colors[colors_idx])
        colors_idx += 1

    plt.legend(comments)
    plt.show()
    

def plot_margins(df_row): 
    dict_data = df_row.to_dict()
    d = dict_data['raw_data']
    uri = dict_data['chum_uri']
    
    init_ts = math.floor(d[0]['timestamp']*1e-4)*1e4
    margins = []
    plt.figure(figsize=(9,7))
    
    t = [x['timestamp']-init_ts for x in d]
    
    plt.subplot(3, 1, 1)
    dist = [x['delta_s'] for x in d]
    plt.plot(t, dist)
    plt.ylabel("Delta Distance (m)")
    plt.legend(['delta_s'])
    
    plt.subplot(3, 1, 2)
    margins = [x['stopping_margin'] for x in d]
    plt.plot(t, margins)
    plt.plot(t, np.zeros(len(t)), 'k--', label='_nolegend_')
    plt.ylabel("Stopping Margin (m)")
        
    plt.subplot(3, 1, 3)
    
    ha = [x['hero_a'] for x in d]
    hv = [x['hero_v'] for x in d]
    ev = [x['entity_v'] for x in d]
    
    leg = ['hero_a', 'hero_v', 'entity_v']
    
    plt.plot(t, ha)
    plt.plot(t, hv)
    plt.plot(t, ev)
    plt.legend(leg)
    plt.show()
    
    url_chum = urllib.quote_plus(uri)
    layout = "layout=eyJsYXlvdXQiOiJmdWxsc2NyZWVuIiwid2lkZ2V0cyI6W3sibmFtZSI6IlhSYXlWaWRlbyIsIm9wdGlvbnMiOnsibmFtZSI6IkZyb250LVZpZXcifSwiZ3JpZE9wdGlvbnMiOnsieCI6OCwieSI6MCwidyI6NCwiaCI6Nn19XSwicGxheWJhY2tSYXRlIjoxfQ%3D%3D"
    argus = lambda uri: "https://argus.zooxlabs.com/uri?primaryUri={}&{}".format(uri, layout)
    return IFrame(argus(uri), width=700, height=600)



In [ ]:
plot_dist([df.min_stopping_margin],
          ['min_margin'], 
          title="Stopping Margin", 
          xlabel="min stopping margin (m)")

In [ ]:
# plot_dist([df.hero_acceleration_min_margin, df.hero_velocity_min_margin, df.distance_min_margin],
#           ['hero_acc', 'hero_v', 'distance'], 
#           title="Hero States", 
#           xlabel="")
plot_dist([df.hero_velocity_min_margin, df.distance_min_margin],
          ['hero_v', 'distance'], 
          title="Hero States", 
          xlabel="")

In [ ]:
autodf = df[df.in_autonomous_mode == True]
manualdf = df[df.in_autonomous_mode == False]

In [ ]:
compare_distributions_plot([autodf, manualdf],
                           ['hero_velocity_min_margin', 'min_stopping_margin'],
                           comments=['auto', 'manual'])

In [ ]:
compare_distributions_plot([autodf, manualdf],
                           ['distance_min_margin', 'min_stopping_margin'],
                           comments=['auto', 'manual'])

In [ ]:
extreme = autodf[autodf.min_stopping_margin < 1]
extreme

In [ ]:
plot_margins(extreme.iloc[3])